In [1]:
!pip install uv
!rm -rf LLaMA-Factory
!git clone --depth 1 https://github.com/hiyouga/LLaMA-Factory.git
%cd LLaMA-Factory
%ls -lah
!uv pip install --system -e '.[torch,bitsandbytes]' wandb pandas numpy liger-kernel --upgrade --quiet
!wget 'https://huggingface.co/datasets/isaiahbjork/chain-of-thought/resolve/main/cot-2.parquet'

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.8/17.8 MB 80.7 MB/s eta 0:00:00
Cloning into 'LLaMA-Factory'...
remote: Enumerating objects: 360, done.
remote: Counting objects: 100% (360/360), done.
remote: Compressing objects: 100% (279/279), done.
remote: Total 360 (delta 79), reused 274 (delta 66), pack-reused 0 (from 0)
Receiving objects: 100% (360/360), 9.94 MiB | 34.87 MiB/s, done.
Resolving deltas: 100% (79/79), done.
/kaggle/working/LLaMA-Factory
total 240K
drwxr-xr-x 12 root root 4.0K Jun 19 14:53 ./
drwxr-xr-x  3 root root 4.0K Jun 19 14:53 ../
drwxr-xr-x  2 root root 4.0K Jun 19 14:53 assets/
-rw-r--r--  1 root root 1.4K Jun 19 14:53 CITATION.cff
drwxr-xr-x  6 root root 4.0K Jun 19 14:53 data/
drwxr-xr-x  5 root root 4.0K Jun 19 14:53 docker/
-rw-r--r--  1 root root  132 Jun 19 14:53 .dockerignore
-rw-r--r--  1 root root  678 Jun 19 14:53 .env.local
drwxr-xr-x  5 root root 4.0K Jun 19 14:53 evaluation/
drwxr-xr-x 10 root root 4.0K Jun 19 14:53 examples/
drwxr-xr-x  8 root ro

In [2]:
from kaggle_secrets import UserSecretsClient
import os
os.environ['HF_TOKEN'] = UserSecretsClient().get_secret('HF_TOKEN')
os.environ['WANDB_API_KEY'] = UserSecretsClient().get_secret('WANDB_API_KEY')

In [3]:
import torch
assert torch.cuda.is_available() is True

import wandb
wandb.login()

wandb: Currently logged in as: aspy1337 (4spy1337) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

In [4]:
import pandas as pd
df = pd.read_parquet('cot-2.parquet').iloc[:, :2]
df['response'] = df['response'].str.replace('<thinking>', '<think>')
df['response'] = df['response'].str.replace('</thinking>', '</think>')
df['response'] = df['response'].str.replace('<output>', '')
df['input'] = ''
df.columns = ['instruction', 'output', 'input']
df

instruction  \
0     Explain the difference between truth and justi...   
1     How can I teach critical thinking skills to my...   
2     I'm facing a difficult problem at work and I'm...   
3     Explain the concept of mental time travel and ...   
4     Explain the concept of ambiguity aversion in d...   
...                                                 ...   
7138  What are some ethical considerations for novel...   
7139  Explain the concept of procrastination from a ...   
7140  What is EQ and how does it compare to IQ in te...   
7141  Explain the key differences between Piaget's a...   
7142  Explain how our perception of identity can imp...   

                                                 output input  
0     <think>\n<initial_analysis>\nTask: Explain the...        
1     <think>\n<initial_analysis>\nTask: Provide met...        
2     <think>\n<initial_analysis>\nTask: Guide the u...        
3     <think>\n<initial_analysis>\nTask: Explain men...        
4     <think>\n<initial_analysis>\nTask: Explain amb...        
...                                                 ...   ...  
7138  <think>\n<tokenization>\nInput: "What are some...        
7139  <think>\n<initial_analysis>\nTask: Explain pro...        
7140  <think>\n<initial_analysis>\nTask: Explain EQ,...        
7141  <think>\n<initial_analysis>\nTask: Compare Pia...        
7142  <think>\n<initial_analysis>\nTask: Explain the...        

[7143 rows x 3 columns]

In [5]:
import json
%cd /kaggle/working/LLaMA-Factory/

dataset = []
for rowidx, row in df.iterrows():
    dataset.append({
        "instruction": row["instruction"],
        "input": row['input'],
        "output": row["output"]
    })

with open("data/identity.json", "w", encoding="utf-8") as f:
  json.dump(dataset, f, indent=2, ensure_ascii=False)

dataset

/kaggle/working/LLaMA-Factory


[{'instruction': 'Explain the difference between truth and justification in epistemology. How can these concepts lead to different combinations of true/false beliefs and justified/unjustified beliefs? Provide examples for each possible combination.',
  'input': '',
  'output': "<think>\n<initial_analysis>\nTask: Explain the difference between truth and justification in epistemology and provide examples of different belief combinations\nApproach: Break down concepts, analyze relationships, and provide examples\nComplexity: Moderate to High\n</initial_analysis>\n\n<conscious_thought>\nI need to clearly distinguish between truth and justification, explain their relationship, and then systematically cover all possible combinations of true/false and justified/unjustified beliefs with examples.\n</conscious_thought>\n\n<step_by_step>\n1. Define truth:\n   - Corresponds to reality\n   - Binary (true or false)\n   - Absolute (not relative to persons, times, places, or cultures)\n\n2. Define ju

In [6]:
# %cd /kaggle/working/LLaMA-Factory/
# !GRADIO_SHARE=1 llamafactory-cli webui

In [7]:
!llamafactory-cli train \
    --stage sft \
    --do_train True \
    --model_name_or_path deepseek-ai/DeepSeek-R1-Distill-Qwen-7B \
    --preprocessing_num_workers 3 \
    --finetuning_type lora \
    --template deepseekr1 \
    --flash_attn auto \
    --enable_liger_kernel True \
    --dataset_dir data \
    --dataset identity \
    --cutoff_len 2048 \
    --learning_rate 5e-05 \
    --num_train_epochs 3.0 \
    --max_samples 100000 \
    --per_device_train_batch_size 4 \
    --gradient_accumulation_steps 8 \
    --lr_scheduler_type cosine \
    --max_grad_norm 1.0 \
    --logging_steps 1 \
    --save_steps 100 \
    --warmup_steps 0 \
    --packing False \
    --train_on_prompt True \
    --enable_thinking True \
    --report_to wandb \
    --output_dir saves/DeepSeek-R1-7B-Distill/lora/train_2025-06-19-04-15-15 \
    --fp16 True \
    --plot_loss True \
    --trust_remote_code True \
    --ddp_timeout 180000000 \
    --include_num_input_tokens_seen True \
    --optim adamw_torch \
    --quantization_bit 4 \
    --quantization_method bnb \
    --double_quantization True \
    --lora_rank 4 \
    --lora_alpha 16 \
    --lora_dropout 0.001 \
    --lora_target all \
    --val_size 0.1 \
    --eval_strategy steps \
    --eval_steps 100 \
    --per_device_eval_batch_size 1

2025-06-19 14:54:54.875700: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1750344895.080717     136 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1750344895.145526     136 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
AttributeError: 'MessageFactory' object has no attribute 'GetPrototype'
AttributeError: 'MessageFactory' object has no attribute 'GetPrototype'
AttributeError: 'MessageFactory' object has no attribute 'GetPrototype'
AttributeError: 'MessageFactory' object has no attribute 'GetPrototype'
AttributeError: 'MessageFactory' object has no attribute 'GetPrototype'
/usr/local/lib/python3.11/dist-packages/jieba/_compat.py:18: UserWarning: pkg